### Importing all the required libraries

In [45]:
import pandas as pd
import numpy as np
import json
import requests
import geocoder
from sklearn.cluster import KMeans
import folium
from bs4 import BeautifulSoup
from geopy.geocoders import Nominatim 

### Scraping website to get neighborhoods of pune city

In [46]:
url="https://en.wikipedia.org/wiki/Template:Neighbourhoods_of_Pune"
data=requests.get(url).text
neighbor_data=BeautifulSoup(data,'lxml')
print(neighbor_data.prettify())

<!DOCTYPE html>
<html class="client-nojs" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Template:Neighbourhoods of Pune - Wikipedia
  </title>
  <script>
   document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"3ed801e2-97dd-43a9-a336-4d36829b72a1","wgCSPNonce":!1,"wgCanonicalNamespace":"Template","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":10,"wgPageName":"Template:Neighbourhoods_of_Pune","wgTitle":"Neighbourhoods of Pune","wgCurRevisionId":941587668,"wgRevisionId":941587668,"wgArticleId":26322286,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Neighbourhoods in Pune"],"wgPageContentLanguage":"en","wgPageContentModel":"wikitext","wgRelevan

#### Adding some more neighborhoods of Pune that were left in the data

In [47]:
column=['Neighborhood']
Neighbour=pd.DataFrame(columns=column)
table=neighbor_data.find('td',class_="navbox-list navbox-odd hlist")
for a in table.find_all('a'):
    if a.text:
       Neighbour=Neighbour.append({'Neighborhood':a.text},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Dhankawadi'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Nigdi'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Lavale Village'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Mulshi'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Akurdi'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Fergusson College Road'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Model Colony'},ignore_index=True)
Neighbour=Neighbour.append({'Neighborhood':'Shivaji Nagar'},ignore_index=True)    
Neighbour=Neighbour.append({'Neighborhood':'Deccan'},ignore_index=True) 
Neighbour=Neighbour.sort_values('Neighborhood')
Neighbour.reset_index(drop=True)



Neighborhood
0                   Akurdi
1                    Aundh
2                 Balewadi
3                    Baner
4                  Bavdhan
5                  Bhosari
6                     Camp
7                   Chakan
8          Charholi Budruk
9                Chinchwad
10                  Dapodi
11                  Deccan
12                    Dehu
13    Dehu Road Cantonment
14              Dhankawadi
15                 Dhayari
16  Fergusson College Road
17                Hadapsar
18               Hinjawadi
19                Kalewadi
20           Kalyani Nagar
21       Khadki cantonment
22                 Kharadi
23           Koregaon Park
24                 Kothrud
25          Lavale Village
26                  Manjri
27            Model Colony
28                  Mulshi
29                  Nanded
30                   Nigdi
31                  Pashan
32                    Paud
33            Pimple Gurav
34         Pimple Saudagar
35                  Pimpri
36                Rahatani
37                   Ravet
38                  Sangvi
39      Sant Tukaram Nagar
40           Shivaji Nagar
41            Shivajinagar
42                     Sus
43                Swargate
44                Thergaon
45             Viman Nagar
46                   Wakad
47                Wanowrie
48                   Warje
49                Yerawada

### Getting latitude and longitude of each neighbour via geocoder

In [48]:
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Pune, India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords
# Call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in Neighbour["Neighborhood"].tolist()]


In [49]:
# Create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])
# Merge the coordinates into the original dataframe
Neighbour['Latitude'] = df_coords['Latitude']
Neighbour['Longitude'] = df_coords['Longitude']
print(Neighbour.shape)
Neighbour

(50, 3)


Neighborhood   Latitude  Longitude
45                  Akurdi  18.565220  73.913910
0                    Aundh  18.764080  73.695730
1                 Balewadi  18.563450  73.812270
2                    Baner  18.576020  73.779830
3                  Bavdhan  18.548200  73.773160
4                  Bhosari  18.507470  73.782360
5                     Camp  18.638730  73.837480
6                   Chakan  18.524590  73.878800
7          Charholi Budruk  18.734150  73.858560
8                Chinchwad  18.640720  73.903970
9                   Dapodi  18.647410  73.800020
49                  Deccan  18.569060  73.881590
11                    Dehu  18.519570  73.835740
10    Dehu Road Cantonment  18.494410  74.398570
41              Dhankawadi  18.537230  73.838080
12                 Dhayari  18.698410  73.749500
46  Fergusson College Road  18.604000  73.750380
13                Hadapsar  18.678880  73.724820
14               Hinjawadi  18.466280  73.853250
15                Kalewadi  18.447020  73.807570
16           Kalyani Nagar  18.530681  73.844239
17       Khadki cantonment  18.502460  73.927160
18                 Kharadi  18.591420  73.738950
19           Koregaon Park  18.394240  74.050880
20                 Kothrud  18.546460  73.900670
43          Lavale Village  18.499030  73.858430
21                  Manjri  18.569210  73.845660
47            Model Colony  18.495380  73.900080
44                  Mulshi  18.614410  73.773850
22                  Nanded  18.544620  73.939220
42                   Nigdi  18.546700  73.751130
23                  Pashan  18.535330  73.893820
24                    Paud  18.505170  73.802450
25            Pimple Gurav  18.501360  73.727680
26         Pimple Saudagar  18.558740  73.987370
27                  Pimpri  18.530710  73.840280
28                Rahatani  18.607080  73.723240
29                   Ravet  18.456420  73.792000
30                  Sangvi  18.659140  73.771400
31      Sant Tukaram Nagar  18.536740  73.792900
48           Shivaji Nagar  18.472110  73.802130
32            Shivajinagar  18.524110  73.615760
33                     Sus  18.589000  73.818150
34                Swargate  18.598540  73.800240
35                Thergaon  18.347100  74.205100
36             Viman Nagar  18.604660  73.787250
37                   Wakad  18.653650  73.744730
38                Wanowrie  18.167560  73.687010
39                   Warje  18.582770  73.985960
40                Yerawada  18.537230  73.838080


### Using FOURSQUARE to get venues at each neighborhood

In [50]:
CLIENT_ID = 'ROWO3FEENYIKSG5PLO04KNTQPOAWGOCSWZ1XSJADC1MOIMHY' # Put Your Client Id
CLIENT_SECRET = 'BELNUT4PTLW5D0B50RTTQG00F2XAMWMFQIHGYOIC03TJNTEV' # Put You Client Secret 
VERSION = '20210707'
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: Hidden')
print('CLIENT_SECRET: Hidden')

Your credentails:
CLIENT_ID: Hidden
CLIENT_SECRET: Hidden


In [51]:
LIMIT=100
def getNearbyVenues( neighborhoods, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for neighborhood, lat, lng in zip( neighborhoods, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        print(results)
        
        # return only relevant information for each nearby venue
        venues_list.append([(
        
            neighborhood, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = [
                  
                  'Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [52]:
neighborhood_venues = getNearbyVenues(
                                             neighborhoods=Neighbour['Neighborhood'],
                                             latitudes=Neighbour['Latitude'],
                                             longitudes=Neighbour['Longitude'])

[{'reasons': {'count': 0, 'items': [{'summary': 'This spot is popular', 'type': 'general', 'reasonName': 'globalInteractionReason'}]}, 'venue': {'id': '5104f72fe4b0b154d1eeb637', 'name': 'Chopsticks Spice Malabar', 'location': {'address': 'Vimannagar', 'crossStreet': 'Datta mandir chowk', 'lat': 18.565244525751083, 'lng': 73.91311556130246, 'labeledLatLngs': [{'label': 'display', 'lat': 18.565244525751083, 'lng': 73.91311556130246}], 'distance': 83, 'cc': 'IN', 'city': 'Pune', 'state': 'Mahārāshtra', 'country': 'India', 'formattedAddress': ['Vimannagar (Datta mandir chowk)', 'Pune', 'Mahārāshtra', 'India']}, 'categories': [{'id': '4bf58dd8d48988d14f941735', 'name': 'Southern / Soul Food Restaurant', 'pluralName': 'Southern / Soul Food Restaurants', 'shortName': 'Southern / Soul', 'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/southern_', 'suffix': '.png'}, 'primary': True}], 'photos': {'count': 0, 'groups': []}}, 'referralId': 'e-0-5104f72fe4b0b154d1eeb637-0'}, {'reaso

In [53]:
pd.set_option('display.max_columns', None) #to display all the columns of table
pd.set_option('display.max_rows', None) #to display all the rows of table

neighborhood_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                    Akurdi              18.565220               73.913910   
1                    Akurdi              18.565220               73.913910   
2                    Akurdi              18.565220               73.913910   
3                    Akurdi              18.565220               73.913910   
4                    Akurdi              18.565220               73.913910   
5                    Akurdi              18.565220               73.913910   
6                    Akurdi              18.565220               73.913910   
7                    Akurdi              18.565220               73.913910   
8                    Akurdi              18.565220               73.913910   
9                    Akurdi              18.565220               73.913910   
10                   Akurdi              18.565220               73.913910   
11                   Akurdi              18.565220               73.913910   
12                   Akurdi              18.565220               73.913910   
13                   Akurdi              18.565220               73.913910   
14                   Akurdi              18.565220               73.913910   
15                   Akurdi              18.565220               73.913910   
16                   Akurdi              18.565220               73.913910   
17                   Akurdi              18.565220               73.913910   
18                   Akurdi              18.565220               73.913910   
19                   Akurdi              18.565220               73.913910   
20                   Akurdi              18.565220               73.913910   
21                   Akurdi              18.565220               73.913910   
22                   Akurdi              18.565220               73.913910   
23                   Akurdi              18.565220               73.913910   
24                   Akurdi              18.565220               73.913910   
25                   Akurdi              18.565220               73.913910   
26                   Akurdi              18.565220               73.913910   
27                   Akurdi              18.565220               73.913910   
28                   Akurdi              18.565220               73.913910   
29                   Akurdi              18.565220               73.913910   
30                   Akurdi              18.565220               73.913910   
31                   Akurdi              18.565220               73.913910   
32                   Akurdi              18.565220               73.913910   
33                   Akurdi              18.565220               73.913910   
34                   Akurdi              18.565220               73.913910   
35                   Akurdi              18.565220               73.913910   
36                   Akurdi              18.565220               73.913910   
37                   Akurdi              18.565220               73.913910   
38                   Akurdi              18.565220               73.913910   
39                   Akurdi              18.565220               73.913910   
40                   Akurdi              18.565220               73.913910   
41                   Akurdi              18.565220               73.913910   
42                   Akurdi              18.565220               73.913910   
43                   Akurdi              18.565220               73.913910   
44                   Akurdi              18.565220               73.913910   
45                 Balewadi              18.563450               73.812270   
46                 Balewadi              18.563450               73.812270   
47                 Balewadi              18.563450               73.812270   
48                 Balewadi              18.563450               73.812270   
49                 Balewadi              18.563450               73.812270   
50                 Balewadi          

In [54]:
# displaying the first venue of each neighborhood
grouped=neighborhood_venues.groupby('Neighborhood')
grouped.first()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                            
Akurdi                              18.565220               73.913910   
Balewadi                            18.563450               73.812270   
Baner                               18.576020               73.779830   
Bavdhan                             18.548200               73.773160   
Bhosari                             18.507470               73.782360   
Camp                                18.638730               73.837480   
Chakan                              18.524590               73.878800   
Dapodi                              18.647410               73.800020   
Deccan                              18.569060               73.881590   
Dehu                                18.519570               73.835740   
Dhankawadi                          18.537230               73.838080   
Fergusson College Road              18.604000               73.750380   
Hinjawadi                           18.466280               73.853250   
Kalewadi                            18.447020               73.807570   
Kalyani Nagar                       18.530681               73.844239   
Khadki cantonment                   18.502460               73.927160   
Kharadi                             18.591420               73.738950   
Kothrud                             18.546460               73.900670   
Lavale Village                      18.499030               73.858430   
Model Colony                        18.495380               73.900080   
Mulshi                              18.614410               73.773850   
Nanded                              18.544620               73.939220   
Pashan                              18.535330               73.893820   
Paud                                18.505170               73.802450   
Pimple Saudagar                     18.558740               73.987370   
Pimpri                              18.530710               73.840280   
Rahatani                            18.607080               73.723240   
Ravet                               18.456420               73.792000   
Sangvi                              18.659140               73.771400   
Sant Tukaram Nagar                  18.536740               73.792900   
Shivajinagar                        18.524110               73.615760   
Sus                                 18.589000               73.818150   
Swargate                            18.598540               73.800240   
Viman Nagar                         18.604660               73.787250   
Warje                               18.582770               73.985960   
Yerawada                            18.537230               73.838080   

                                                                    Venue  \
Neighborhood                                                                
Akurdi                                           Chopsticks Spice Malabar   
Balewadi                                           Picantos Mexican Grill   
Baner                                                  The Chocolate Room   
Bavdhan                                                           Rastafa   
Bhosari                                                   Cafe Coffee Day   
Camp                                            Sanket Restaurant and Bar   
Chakan                                                         Poona Club   
Dapodi                  Tata Motors Cars Service Centre - Panchjanya A...   
Deccan                                                     Domino's Pizza   
Dehu                                                     Panchvati Gaurav   
Dhankawadi                                                           Kiva   
Fergusson College Road                                    Cafe Coffee Day   
Hinjawadi                                          SKS Katthi Kabab Rolls   
Kalewadi                                                           Nisarg   
Kalyani Nagar    

In [55]:
venues=neighborhood_venues.groupby('Neighborhood').count()
venues

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                   
Akurdi                                     45                      45     45   
Balewadi                                   16                      16     16   
Baner                                       3                       3      3   
Bavdhan                                     3                       3      3   
Bhosari                                    13                      13     13   
Camp                                        1                       1      1   
Chakan                                     19                      19     19   
Dapodi                                      3                       3      3   
Deccan                                      5                       5      5   
Dehu                                        6                       6      6   
Dhankawadi                                 15                      15     15   
Fergusson College Road                      5                       5      5   
Hinjawadi                                   5                       5      5   
Kalewadi                                    5                       5      5   
Kalyani Nagar                              12                      12     12   
Khadki cantonment                           7                       7      7   
Kharadi                                     7                       7      7   
Kothrud                                    14                      14     14   
Lavale Village                              5                       5      5   
Model Colony                                7                       7      7   
Mulshi                                      5                       5      5   
Nanded                                      4                       4      4   
Pashan                                     17                      17     17   
Paud                                        7                       7      7   
Pimple Saudagar                             1                       1      1   
Pimpri                                     23                      23     23   
Rahatani                                    2                       2      2   
Ravet                                       2                       2      2   
Sangvi                                     13                      13     13   
Sant Tukaram Nagar                          5                       5      5   
Shivajinagar                                1                       1      1   
Sus                                         5                       5      5   
Swargate                                    2                       2      2   
Viman Nagar                                 4                       4      4   
Warje                                       3                       3      3   
Yerawada                                   15                      15     15   

                        Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                             
Akurdi                              45               45              45  
Balewadi                            16               16              16  
Baner                                3                3               3  
Bavdhan                              3                3               3  
Bhosari                             13               13              13  
Camp                                 1                1               1  
Chakan                              19               19              19  
Dapodi                               3                3               3  
Deccan                               5                5               5  
Dehu                                 6                6               6  
Dhankawadi                          15               15              15  
Fergusson College Roa

### Mapping the venues and their neighborhoods using geolocator

In [56]:
address= 'Pune, India'
geolocator= Nominatim(user_agent="Pune-explorer")
location=geolocator.geocode(address)
latitude=location.latitude
longitude= location.longitude
print("The coordinates of the Pune are {},{} .".format(latitude,longitude))

The coordinates of the Pune are 18.521428,73.8544541 .


In [57]:
map_Pune = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lng, venue, neighborhood in zip(neighborhood_venues['Venue Latitude'], neighborhood_venues['Venue Longitude'],neighborhood_venues['Venue'],  neighborhood_venues['Neighborhood']):
    label = '{}, {}'.format(neighborhood, venue)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_Pune)
map_Pune

### Scraping the data of webpage that consists of main colleges in Pune

In [58]:
url="https://www.shiksha.com/colleges/pune-3"
data=requests.get(url).text
college_data=BeautifulSoup(data,'lxml')
print(college_data.prettify())

<!DOCTYPE html>
<html>
 <head>
  <meta charset="utf-8"/>
  <meta content="IE=edge" http-equiv="X-UA-Compatible"/>
  <title id="seoTitle">
   Colleges in Pune - Reviews, Fees, Ranks &amp; Admissions of all Pune colleges at Shiksha
  </title>
  <meta content="Shiksha, education, colleges,universities, institutes,career, career options, career prospects,engineering, mba, medical, mbbs,study abroad, foreign education, college, university, institute,courses, coaching, technical education, higher education,forum, community, education career experts,ask experts, admissions,results, events,scholarships" name="keywords"/>
  <meta content="Find list of all top 1259 colleges in Pune at Shiksha.com. Check Fees, Admission process, Discussion, Reviews and Placements of all Pune colleges listed on Shiksha" id="metaDescription" name="description"/>
  <link href="https://www.shiksha.com/colleges/pune" id="canonicalUrl" rel="canonical"/>
  <link href="https://www.shiksha.com/colleges/pune-2" rel="prev"/

In [59]:
column=['Colleges','Neighborhood']
college=pd.DataFrame(columns=column)

content=college_data.find('div',id='rspnsv-tpl')
collegesname=0
location=0
for table in content.find_all('div',{"class":"elipsysBox"}):
                    
        collegesname=table.h2.text
        
    
        Neighborhood=table.span.text[:-6]
        college=college.append({'Neighborhood':Neighborhood,'Colleges':collegesname},ignore_index=True)
        
college.sort_values('Neighborhood')  
college.dropna(axis=0)
#Adding some more colleges that were left
college=college.append({'Colleges':'Symbiosis International University','Neighborhood':'Lavale Village'},ignore_index=True)
college=college.append({'Colleges':'Bharati Vidyapeeth College of Engineering','Neighborhood':'Dhankawadi'},ignore_index=True)
college=college.append({'Colleges':'Bharati Vidyapeeth Medical College','Neighborhood':'Dhankawadi'},ignore_index=True)
college=college.append({'Colleges':'Yashwantrao Mohite College','Neighborhood':'Kothrud'},ignore_index=True)
college=college.append({'Colleges':'Symbiosis Institute of International Business (SIIB)','Neighborhood':'Hinjewadi'},ignore_index=True)
college=college.append({'Colleges':'Symbiosis Law School (SLS), Pune','Neighborhood':'Viman Nagar'},ignore_index=True)
college=college.append({'Colleges':'SICSR','Neighborhood':'Model Colony'},ignore_index=True)
college

Colleges  \
0                                Pune Business School   
1                  RIIM - Arihant Group of Institutes   
2                            MIT SOM College, MIT WPU   
3                        Christ - lavasa, Pune Campus   
4   Jayawantrao Sawant Institute of Management and...   
5   Dr. D.Y. Patil Vidyapeeth Global Business Scho...   
6         Frankfinn Institute of Air Hostess Training   
7                         Government Polytechnic Pune   
8          Indian School of Technology and Management   
9      VIT Pune - Vishwakarma Institute of Technology   
10  Institute of Industrial and Computer Managemen...   
11    Dr. D. Y. Patil Institute of Management Studies   
12                 AIT - Army Institute of Technology   
13                            Dr. D.Y. Patil B-School   
14                                   FLAME University   
15      International Institute of Management Studies   
16  ICSI Delhi - Institute of Company Secretaries ...   
17  Lexicon Management Institute of Leadership and...   
18  ASM's Institute of Business Management and Res...   
19  Dr. D. Y. Patil College of Agriculture Busines...   
20  NMIMS Global Access School for Continuing Educ...   
21      NIEM- The Institute of Event Management, Pune   
22          Jayawantrao Sawant College of Engineering   
23                 Dr. D.Y. Patil College of Pharmacy   
24          Symbiosis Institute of Management Studies   
25                     MITCON Institute of Management   
26                 School of Distance Education, Pune   
27              Symbiosis Statistical Institute, Pune   
28                          School of Design, MIT WPU   
29  Sai Balaji International Institute of Manageme...   
30                 Symbiosis International University   
31          Bharati Vidyapeeth College of Engineering   
32                 Bharati Vidyapeeth Medical College   
33                         Yashwantrao Mohite College   
34  Symbiosis Institute of International Business ...   
35                   Symbiosis Law School (SLS), Pune   
36                                              SICSR   

                Neighborhood  
0                      Nigdi  
1                    Bavdhan  
2                    Kothrud  
3                     Mulshi  
4                   Hadapsar  
5                  Tathawade  
6                    Kothrud  
7              Shivaji Nagar  
8                  Chinchwad  
9                  Bibwewadi  
10                     Nigdi  
11                     Nigdi  
12               Dighi hills  
13                 Tathawade  
14            Lavale Village  
15                 Hinjewadi  
16                            
17                   Wagholi  
18                 Chinchwad  
19                    Akurdi  
20                    Deccan  
21    Fergusson College Road  
22                  Hadapsar  
23                    Akurdi  
24                    Khadki  
25                  Balewadi  
26  Lal Bahadur Shastri Marg  
27       Senapati Bapat Road  
28                   Kothrud  
29                 Hinjewadi  
30            Lavale Village  
31                Dhankawadi  
32                Dhankawadi  
33                   Kothrud  
34                 Hinjewadi  
35               Viman Nagar  
36              Model Colony

#### Merging two dataframes; one of college list and other one is of neighborhood and their latitudes and longitudes

In [60]:
df=pd.merge(college,Neighbour,how='inner',on='Neighborhood')
df=df.sort_values('Neighborhood')
df.set_index('Neighborhood')

Colleges  \
Neighborhood                                                                
Akurdi                                 Dr. D.Y. Patil College of Pharmacy   
Akurdi                  Dr. D. Y. Patil College of Agriculture Busines...   
Balewadi                                   MITCON Institute of Management   
Bavdhan                                RIIM - Arihant Group of Institutes   
Chinchwad               ASM's Institute of Business Management and Res...   
Chinchwad                      Indian School of Technology and Management   
Deccan                  NMIMS Global Access School for Continuing Educ...   
Dhankawadi                             Bharati Vidyapeeth Medical College   
Dhankawadi                      Bharati Vidyapeeth College of Engineering   
Fergusson College Road      NIEM- The Institute of Event Management, Pune   
Hadapsar                Jayawantrao Sawant Institute of Management and...   
Hadapsar                        Jayawantrao Sawant College of Engineering   
Kothrud                                          MIT SOM College, MIT WPU   
Kothrud                       Frankfinn Institute of Air Hostess Training   
Kothrud                                         School of Design, MIT WPU   
Kothrud                                        Yashwantrao Mohite College   
Lavale Village                                           FLAME University   
Lavale Village                         Symbiosis International University   
Model Colony                                                        SICSR   
Mulshi                                       Christ - lavasa, Pune Campus   
Nigdi                     Dr. D. Y. Patil Institute of Management Studies   
Nigdi                   Institute of Industrial and Computer Managemen...   
Nigdi                                                Pune Business School   
Shivaji Nagar                                 Government Polytechnic Pune   
Viman Nagar                              Symbiosis Law School (SLS), Pune   

                        Latitude  Longitude  
Neighborhood                                 
Akurdi                  18.56522   73.91391  
Akurdi                  18.56522   73.91391  
Balewadi                18.56345   73.81227  
Bavdhan                 18.54820   73.77316  
Chinchwad               18.64072   73.90397  
Chinchwad               18.64072   73.90397  
Deccan                  18.56906   73.88159  
Dhankawadi              18.53723   73.83808  
Dhankawadi              18.53723   73.83808  
Fergusson College Road  18.60400   73.75038  
Hadapsar                18.67888   73.72482  
Hadapsar                18.67888   73.72482  
Kothrud                 18.54646   73.90067  
Kothrud                 18.54646   73.90067  
Kothrud                 18.54646   73.90067  
Kothrud                 18.54646   73.90067  
Lavale Village          18.49903   73.85843  
Lavale Village          18.49903   73.85843  
Model Colony            18.49538   73.90008  
Mulshi                  18.61441   73.77385  
Nigdi                   18.54670   73.75113  
Nigdi                   18.54670   73.75113  
Nigdi                   18.54670   73.75113  
Shivaji Nagar           18.47211   73.80213  
Viman Nagar             18.60466   73.78725

In [61]:
df[["Neighborhood","Latitude","Longitude","Colleges"]] # To get columns in definite order

Neighborhood  Latitude  Longitude  \
17                  Akurdi  18.56522   73.91391   
16                  Akurdi  18.56522   73.91391   
20                Balewadi  18.56345   73.81227   
3                  Bavdhan  18.54820   73.77316   
13               Chinchwad  18.64072   73.90397   
12               Chinchwad  18.64072   73.90397   
18                  Deccan  18.56906   73.88159   
22              Dhankawadi  18.53723   73.83808   
21              Dhankawadi  18.53723   73.83808   
19  Fergusson College Road  18.60400   73.75038   
9                 Hadapsar  18.67888   73.72482   
10                Hadapsar  18.67888   73.72482   
4                  Kothrud  18.54646   73.90067   
5                  Kothrud  18.54646   73.90067   
6                  Kothrud  18.54646   73.90067   
7                  Kothrud  18.54646   73.90067   
14          Lavale Village  18.49903   73.85843   
15          Lavale Village  18.49903   73.85843   
24            Model Colony  18.49538   73.90008   
8                   Mulshi  18.61441   73.77385   
2                    Nigdi  18.54670   73.75113   
1                    Nigdi  18.54670   73.75113   
0                    Nigdi  18.54670   73.75113   
11           Shivaji Nagar  18.47211   73.80213   
23             Viman Nagar  18.60466   73.78725   

                                             Colleges  
17                 Dr. D.Y. Patil College of Pharmacy  
16  Dr. D. Y. Patil College of Agriculture Busines...  
20                     MITCON Institute of Management  
3                  RIIM - Arihant Group of Institutes  
13  ASM's Institute of Business Management and Res...  
12         Indian School of Technology and Management  
18  NMIMS Global Access School for Continuing Educ...  
22                 Bharati Vidyapeeth Medical College  
21          Bharati Vidyapeeth College of Engineering  
19      NIEM- The Institute of Event Management, Pune  
9   Jayawantrao Sawant Institute of Management and...  
10          Jayawantrao Sawant College of Engineering  
4                            MIT SOM College, MIT WPU  
5         Frankfinn Institute of Air Hostess Training  
6                           School of Design, MIT WPU  
7                          Yashwantrao Mohite College  
14                                   FLAME University  
15                 Symbiosis International University  
24                                              SICSR  
8                        Christ - lavasa, Pune Campus  
2     Dr. D. Y. Patil Institute of Management Studies  
1   Institute of Industrial and Computer Managemen...  
0                                Pune Business School  
11                        Government Polytechnic Pune  
23                   Symbiosis Law School (SLS), Pune

In [62]:
dataframe=df.groupby('Neighborhood').count()
dataframe

Colleges  Latitude  Longitude
Neighborhood                                         
Akurdi                         2         2          2
Balewadi                       1         1          1
Bavdhan                        1         1          1
Chinchwad                      2         2          2
Deccan                         1         1          1
Dhankawadi                     2         2          2
Fergusson College Road         1         1          1
Hadapsar                       2         2          2
Kothrud                        4         4          4
Lavale Village                 2         2          2
Model Colony                   1         1          1
Mulshi                         1         1          1
Nigdi                          3         3          3
Shivaji Nagar                  1         1          1
Viman Nagar                    1         1          1

### Mapping the college dataframe along with their neighborhoods 

In [63]:
map_PuneColleges = folium.Map(location=[latitude, longitude], zoom_start=11)
for lat, lng, college, neighborhood in zip(df['Latitude'], df['Longitude'],df['Colleges'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, college)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_PuneColleges)
map_PuneColleges

# Methodology

##### In this project, we have to find a suitable location to open a PG or hostel for students

##### Thus, in the first step, we have collected data of neighborhoods in Pune through web scraping followed by finding their latitudes and longitudes via geocoder . Then, we have used Foursquare to find out the venues at each neighborhood and  finally, we have scraped data of colleges in Pune and mapped all these datas .

##### In the next step, we will perform data analysis in order to get information crystal clear about where to open a hostel and will cluster the data through k-means clustering.


## Analysis

##### Let's first analyze each neighborhood and find out more about it each one.



In [92]:
# one hot encoding
neighborhood_onehot = pd.get_dummies(neighborhood_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
neighborhood_onehot['Neighborhood'] = neighborhood_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [neighborhood_onehot.columns[-1]] + list(neighborhood_onehot.columns[:-1])
neighborhood_onehot = neighborhood_onehot[fixed_columns]
pd.set_option('display.max_columns', None) #to display all the columns of table
pd.set_option('display.max_rows', None) #to display all the rows of table

neighborhood_onehot

Neighborhood  ATM  American Restaurant  Asian Restaurant  \
0                    Akurdi    0                    0                 0   
1                    Akurdi    0                    0                 0   
2                    Akurdi    0                    0                 0   
3                    Akurdi    0                    0                 0   
4                    Akurdi    0                    0                 0   
5                    Akurdi    0                    0                 0   
6                    Akurdi    0                    0                 0   
7                    Akurdi    0                    0                 0   
8                    Akurdi    0                    1                 0   
9                    Akurdi    0                    0                 0   
10                   Akurdi    0                    0                 0   
11                   Akurdi    0                    0                 0   
12                   Akurdi    0                    0                 0   
13                   Akurdi    0                    0                 1   
14                   Akurdi    0                    0                 0   
15                   Akurdi    0                    0                 0   
16                   Akurdi    0                    0                 0   
17                   Akurdi    0                    0                 0   
18                   Akurdi    0                    0                 1   
19                   Akurdi    0                    0                 0   
20                   Akurdi    0                    0                 0   
21                   Akurdi    0                    0                 0   
22                   Akurdi    0                    0                 0   
23                   Akurdi    0                    0                 0   
24                   Akurdi    0                    0                 0   
25                   Akurdi    0                    0                 0   
26                   Akurdi    0                    0                 0   
27                   Akurdi    0                    0                 0   
28                   Akurdi    0                    0                 0   
29                   Akurdi    0                    0                 0   
30                   Akurdi    0                    0                 0   
31                   Akurdi    0                    0                 0   
32                   Akurdi    0                    0                 0   
33                   Akurdi    0                    0                 0   
34                   Akurdi    0                    0                 0   
35                   Akurdi    0                    0                 0   
36                   Akurdi    0                    0                 0   
37                   Akurdi    0                    0                 0   
38                   Akurdi    0                    0                 0   
39                   Akurdi    0                    0                 0   
40                   Akurdi    0                    0                 0   
41                   Akurdi    0                    0                 0   
42                   Akurdi    0                    0                 0   
43                   Akurdi    0                    0                 0   
44                   Akurdi    0                    0                 0   
45                 Balewadi    0                    0                 0   
46                 Balewadi    0                    0                 0   
47                 Balewadi    0                    0                 0   
48                 Balewadi    0                    0                 0   
49                 Balewadi    0                    0                 0   
50                 Balewadi    0                    0                 0   
51                 Balewadi    0                    0                 0   
52                 Balewadi    0        

##### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category



In [65]:
venue_mean=neighborhood_onehot.groupby("Neighborhood").mean().reset_index()
venue_mean

Neighborhood  ATM  American Restaurant  Asian Restaurant  \
0                   Akurdi  0.0             0.022222          0.044444   
1                 Balewadi  0.0             0.000000          0.000000   
2                    Baner  0.0             0.000000          0.000000   
3                  Bavdhan  0.0             0.000000          0.000000   
4                  Bhosari  0.0             0.000000          0.076923   
5                     Camp  0.0             0.000000          0.000000   
6                   Chakan  0.0             0.000000          0.000000   
7                   Dapodi  0.0             0.000000          0.000000   
8                   Deccan  0.0             0.000000          0.000000   
9                     Dehu  0.0             0.000000          0.000000   
10              Dhankawadi  0.0             0.000000          0.066667   
11  Fergusson College Road  0.0             0.000000          0.000000   
12               Hinjawadi  0.2             0.000000          0.000000   
13                Kalewadi  0.0             0.000000          0.000000   
14           Kalyani Nagar  0.0             0.000000          0.000000   
15       Khadki cantonment  0.0             0.000000          0.000000   
16                 Kharadi  0.0             0.000000          0.142857   
17                 Kothrud  0.0             0.000000          0.000000   
18          Lavale Village  0.0             0.000000          0.000000   
19            Model Colony  0.0             0.000000          0.000000   
20                  Mulshi  0.2             0.000000          0.000000   
21                  Nanded  0.0             0.000000          0.000000   
22                  Pashan  0.0             0.000000          0.058824   
23                    Paud  0.0             0.000000          0.000000   
24         Pimple Saudagar  1.0             0.000000          0.000000   
25                  Pimpri  0.0             0.000000          0.000000   
26                Rahatani  0.5             0.000000          0.000000   
27                   Ravet  1.0             0.000000          0.000000   
28                  Sangvi  0.0             0.000000          0.076923   
29      Sant Tukaram Nagar  0.0             0.000000          0.000000   
30            Shivajinagar  0.0             0.000000          0.000000   
31                     Sus  0.6             0.000000          0.000000   
32                Swargate  0.0             0.000000          0.000000   
33             Viman Nagar  0.5             0.000000          0.000000   
34                   Warje  0.0             0.000000          0.000000   
35                Yerawada  0.0             0.000000          0.066667   

    Auto Dealership  BBQ Joint    Bakery  Bed & Breakfast  Beer Garden  \
0          0.000000   0.000000  0.000000         0.000000     0.000000   
1          0.000000   0.000000  0.000000         0.000000     0.000000   
2          0.000000   0.000000  0.000000         0.000000     0.000000   
3          0.000000   0.000000  0.000000         0.000000     0.000000   
4          0.000000   0.000000  0.000000         0.076923     0.000000   
5          0.000000   0.000000  0.000000         0.000000     0.000000   
6          0.000000   0.000000  0.000000         0.000000     0.000000   
7          0.333333   0.000000  0.333333         0.000000     0.000000   
8          0.000000   0.000000  0.000000         0.000000     0.000000   
9          0.000000   0.000000  0.000000         0.000000     0.000000   
10         0.000000   0.000000  0.000000         0.000000     0.000000   
11         0.000000   0.000000  0.000000         0.000000     0.000000   
12         0.000000   0.000000  0.000000         0.000000     0.000000   
13         0.000000   0.000000  0.000000         0.000000     0.000000   
14         0.000000   0.083333  0.000000         0.000000     0.000000   
15         0.000000   0.000000  0.000000         0.000000     0.142857   
16         0.0000

In [66]:
venue_mean.shape# size of dataframe

(36, 85)

##### Printing each neighborhood with top 5  most common venues 

In [67]:
num_top_venues = 5

for hood in venue_mean['Neighborhood']:
    print("----"+hood+"----")
    temp = venue_mean[venue_mean['Neighborhood'] == hood].T.reset_index() #T function is to transpose
    temp.columns = ['venue','freq']
    temp = temp.iloc[2:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')
    

----Akurdi----
                     venue  freq
0        Indian Restaurant  0.16
1                     Café  0.13
2              Coffee Shop  0.11
3  South Indian Restaurant  0.04
4           Clothing Store  0.04


----Balewadi----
                  venue  freq
0     Indian Restaurant  0.19
1   Sporting Goods Shop  0.12
2  Fast Food Restaurant  0.12
3           Bus Station  0.06
4     Mobile Phone Shop  0.06


----Baner----
                 venue  freq
0          Coffee Shop  0.33
1                  Gym  0.33
2       Breakfast Spot  0.33
3  American Restaurant  0.00
4   Mexican Restaurant  0.00


----Bavdhan----
                 venue  freq
0    Indian Restaurant  0.33
1   Italian Restaurant  0.33
2             Mountain  0.33
3  American Restaurant  0.00
4   Mexican Restaurant  0.00


----Bhosari----
               venue  freq
0  Indian Restaurant  0.38
1               Café  0.15
2         Restaurant  0.08
3        Coffee Shop  0.08
4         Food Court  0.08


----Camp----
           

##### Now let's create a new dataframe and display the top 10 venues for each neighborhood to find out more about the social characteristics.



In [68]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[2:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [69]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = venue_mean['Neighborhood']

for ind in np.arange(venue_mean.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(venue_mean.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Akurdi     Indian Restaurant                  Café   
1     Balewadi     Indian Restaurant   Sporting Goods Shop   
2        Baner           Coffee Shop                   Gym   
3      Bavdhan     Indian Restaurant    Italian Restaurant   
4      Bhosari     Indian Restaurant                  Café   

  3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0           Coffee Shop  South Indian Restaurant        Clothing Store   
1  Fast Food Restaurant              Bus Station     Mobile Phone Shop   
2        Breakfast Spot      American Restaurant    Mexican Restaurant   
3              Mountain      American Restaurant    Mexican Restaurant   
4            Restaurant              Coffee Shop            Food Court   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0      Asian Restaurant   American Restaurant            Donut Shop   
1        Ice Cream Shop                 Plaza         Grocery Store   
2       Organic Grocery                Office             Multiplex   
3       Organic Grocery                Office             Multiplex   
4            Smoke Shop      Asian Restaurant       Bed & Breakfast   

  9th Most Common Venue   10th Most Common Venue  
0   Dumpling Restaurant  Fruit & Vegetable Store  
1     Korean Restaurant              Snack Place  
2         Movie Theater                 Mountain  
3         Movie Theater                    Motel  
4             Juice Bar                    Motel

#### Now, we'll merge the dataframe of top 10 common venues of neighborhoods with dataframe of neighborhoods with number of famous colleges in Pune

In [74]:
neighborhoods_venuesColleges_sorted=pd.merge(neighborhoods_venues_sorted,dataframe,on="Neighborhood")
Analysed_data=neighborhoods_venuesColleges_sorted.drop(["Latitude","Longitude"],axis=1)
Analysed_data

Neighborhood          1st Most Common Venue  \
0                   Akurdi              Indian Restaurant   
1                 Balewadi              Indian Restaurant   
2                  Bavdhan              Indian Restaurant   
3                   Deccan  Vegetarian / Vegan Restaurant   
4               Dhankawadi                      Multiplex   
5   Fergusson College Road                           Café   
6                  Kothrud                 Breakfast Spot   
7           Lavale Village              Indian Restaurant   
8             Model Colony                    Pizza Place   
9                   Mulshi  Vegetarian / Vegan Restaurant   
10             Viman Nagar           Gym / Fitness Center   

            2nd Most Common Venue      3rd Most Common Venue  \
0                            Café                Coffee Shop   
1             Sporting Goods Shop       Fast Food Restaurant   
2              Italian Restaurant                   Mountain   
3                   Shopping Mall       Fast Food Restaurant   
4               Indian Restaurant                     Lounge   
5                    Home Service  Indian Chinese Restaurant   
6   Vegetarian / Vegan Restaurant          Indian Restaurant   
7                          Bakery                        Gym   
8               Indian Restaurant         Chinese Restaurant   
9                      Restaurant            Bed & Breakfast   
10                           Café        American Restaurant   

      4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0   South Indian Restaurant        Clothing Store      Asian Restaurant   
1               Bus Station     Mobile Phone Shop        Ice Cream Shop   
2       American Restaurant    Mexican Restaurant       Organic Grocery   
3        Chinese Restaurant           Pizza Place    Tex-Mex Restaurant   
4               Coffee Shop        Clothing Store    Chinese Restaurant   
5         Indian Restaurant     Mobile Phone Shop       Organic Grocery   
6               Pizza Place    Italian Restaurant        Ice Cream Shop   
7                    Office   American Restaurant    Mexican Restaurant   
8      Fast Food Restaurant          Dance Studio                 Motel   
9         Mobile Phone Shop    Mexican Restaurant       Organic Grocery   
10       Mexican Restaurant       Organic Grocery                Office   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0    American Restaurant            Donut Shop   Dumpling Restaurant   
1                  Plaza         Grocery Store     Korean Restaurant   
2                 Office             Multiplex         Movie Theater   
3        Organic Grocery             Multiplex         Movie Theater   
4              Bookstore              Pharmacy    Italian Restaurant   
5                 Office             Multiplex         Movie Theater   
6             Restaurant                Lounge     Convenience Store   
7        Organic Grocery             Multiplex         Movie Theater   
8                   Park       Organic Grocery                Office   
9                 Office             Multiplex         Movie Theater   
10             Multiplex         Movie Theater              Mountain   

     10th Most Common Venue  Colleges  
0   Fruit & Vegetable Store         2  
1               Snack Place         1  
2                     Motel         1  
3                  Mountain         1  
4          Asian Restaurant         2  
5                  Mountain         1  
6        Mexican Restaurant         4  
7                  Mountain         2  
8                 Multiplex         1  
9                  Mountain         1  
10                    Motel         1

# K-Means Clustering

##### Lets merge the dataframes of mean values of venues at each neighborhood with the dataframe of  counts of colleges in each neighborhood

In [71]:
data = pd.merge(venue_mean,dataframe, on="Neighborhood")
data.head(10)
#venue_mean = venue_mean.merge(dataframe, left_on='Neighborhood', right_on='Neighborhood').drop(columns=['Neighborhood']).fillna(0)
#venue_mean


Neighborhood  ATM  American Restaurant  Asian Restaurant  \
0                  Akurdi  0.0             0.022222          0.044444   
1                Balewadi  0.0             0.000000          0.000000   
2                 Bavdhan  0.0             0.000000          0.000000   
3                  Deccan  0.0             0.000000          0.000000   
4              Dhankawadi  0.0             0.000000          0.066667   
5  Fergusson College Road  0.0             0.000000          0.000000   
6                 Kothrud  0.0             0.000000          0.000000   
7          Lavale Village  0.0             0.000000          0.000000   
8            Model Colony  0.0             0.000000          0.000000   
9                  Mulshi  0.2             0.000000          0.000000   

   Auto Dealership  BBQ Joint  Bakery  Bed & Breakfast  Beer Garden    Bistro  \
0              0.0        0.0     0.0              0.0          0.0  0.022222   
1              0.0        0.0     0.0              0.0          0.0  0.000000   
2              0.0        0.0     0.0              0.0          0.0  0.000000   
3              0.0        0.0     0.0              0.0          0.0  0.000000   
4              0.0        0.0     0.0              0.0          0.0  0.000000   
5              0.0        0.0     0.0              0.0          0.0  0.000000   
6              0.0        0.0     0.0              0.0          0.0  0.000000   
7              0.0        0.0     0.2              0.0          0.0  0.000000   
8              0.0        0.0     0.0              0.0          0.0  0.000000   
9              0.0        0.0     0.0              0.2          0.0  0.000000   

   Boarding House  Bookstore  Breakfast Spot  Burger Joint  Bus Station  \
0             0.0   0.000000        0.000000           0.0       0.0000   
1             0.0   0.000000        0.000000           0.0       0.0625   
2             0.0   0.000000        0.000000           0.0       0.0000   
3             0.0   0.000000        0.000000           0.0       0.0000   
4             0.0   0.066667        0.000000           0.0       0.0000   
5             0.0   0.000000        0.000000           0.0       0.0000   
6             0.0   0.000000        0.142857           0.0       0.0000   
7             0.0   0.000000        0.000000           0.0       0.0000   
8             0.0   0.000000        0.000000           0.0       0.0000   
9             0.0   0.000000        0.000000           0.0       0.0000   

       Café  Campground  Cheese Shop  Chinese Restaurant  Clothing Store  \
0  0.133333         0.0     0.022222            0.022222        0.044444   
1  0.000000         0.0     0.000000            0.000000        0.000000   
2  0.000000         0.0     0.000000            0.000000        0.000000   
3  0.000000         0.0     0.000000            0.200000        0.000000   
4  0.000000         0.0     0.000000            0.066667        0.066667   
5  0.400000         0.0     0.000000            0.000000        0.000000   
6  0.071429         0.0     0.000000            0.000000        0.000000   
7  0.000000         0.0     0.000000            0.000000        0.000000   
8  0.000000         0.0     0.000000            0.142857        0.000000   
9  0.000000         0.0     0.000000            0.000000        0.000000   

   Coffee Shop  Convenience Store  Cosmetics Shop  Creperie  Dance Studio  \
0     0.111111           0.000000             0.0       0.0      0.000000   
1     0.000000           0.000000             0.0       0.0      0.000000   
2     0.000000           0.000000             0.0       0.0      0.000000   
3     0.000000           0.000000             0.0       0.0      0.000000   
4     0.066667           0.000000             0.0       0.0      0.000000   
5     0.000000           0.000000             0.0       0.0      0.000000   
6     0.000000           0.071429             0.0       0.0      0.000000   
7     0.000000           0.000000     

##### Run k-means to cluster the neighborhood into 5 clusters.



In [72]:
# set number of clusters
kclusters = 5

clustering = data.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 3, 4, 3, 0, 1, 2, 0, 3, 3])

##### Let's create a new dataframe that includes the cluster as well as the top 10 venues and colleges for each neighborhood.



In [88]:
# add clustering labels
Analysed_data['Cluster Labels'] = kmeans.labels_
#cluster=neighborhoods_venuesColleges_sorted.drop(["Latitude","Longitude"],axis=1)
#cluster


Pune_merged = Neighbour.copy()

# merge toronto_grouped with df_toronto_borough to add latitude/longitude for each neighborhood
Pune_merged= Pune_merged.join(Analysed_data.set_index('Neighborhood'), on='Neighborhood').dropna()
Pune_merged['Cluster Labels']=Pune_merged['Cluster Labels'].astype(int)
Pune_merged['Colleges']=Pune_merged['Colleges'].astype(int)
Pune_merged.reset_index(drop=True).head(11) # check the last columns!

Neighborhood  Latitude  Longitude  \
0                   Akurdi  18.56522   73.91391   
1                 Balewadi  18.56345   73.81227   
2                  Bavdhan  18.54820   73.77316   
3                   Deccan  18.56906   73.88159   
4               Dhankawadi  18.53723   73.83808   
5   Fergusson College Road  18.60400   73.75038   
6                  Kothrud  18.54646   73.90067   
7           Lavale Village  18.49903   73.85843   
8             Model Colony  18.49538   73.90008   
9                   Mulshi  18.61441   73.77385   
10             Viman Nagar  18.60466   73.78725   

            1st Most Common Venue          2nd Most Common Venue  \
0               Indian Restaurant                           Café   
1               Indian Restaurant            Sporting Goods Shop   
2               Indian Restaurant             Italian Restaurant   
3   Vegetarian / Vegan Restaurant                  Shopping Mall   
4                       Multiplex              Indian Restaurant   
5                            Café                   Home Service   
6                  Breakfast Spot  Vegetarian / Vegan Restaurant   
7               Indian Restaurant                         Bakery   
8                     Pizza Place              Indian Restaurant   
9   Vegetarian / Vegan Restaurant                     Restaurant   
10           Gym / Fitness Center                           Café   

        3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0                 Coffee Shop  South Indian Restaurant        Clothing Store   
1        Fast Food Restaurant              Bus Station     Mobile Phone Shop   
2                    Mountain      American Restaurant    Mexican Restaurant   
3        Fast Food Restaurant       Chinese Restaurant           Pizza Place   
4                      Lounge              Coffee Shop        Clothing Store   
5   Indian Chinese Restaurant        Indian Restaurant     Mobile Phone Shop   
6           Indian Restaurant              Pizza Place    Italian Restaurant   
7                         Gym                   Office   American Restaurant   
8          Chinese Restaurant     Fast Food Restaurant          Dance Studio   
9             Bed & Breakfast        Mobile Phone Shop    Mexican Restaurant   
10        American Restaurant       Mexican Restaurant       Organic Grocery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0       Asian Restaurant   American Restaurant            Donut Shop   
1         Ice Cream Shop                 Plaza         Grocery Store   
2        Organic Grocery                Office             Multiplex   
3     Tex-Mex Restaurant       Organic Grocery             Multiplex   
4     Chinese Restaurant             Bookstore              Pharmacy   
5        Organic Grocery                Office             Multiplex   
6         Ice Cream Shop            Restaurant                Lounge   
7     Mexican Restaurant       Organic Grocery             Multiplex   
8                  Motel                  Park       Organic Grocery   
9        Organic Grocery                Office             Multiplex   
10                Office             Multiplex         Movie Theater   

   9th Most Common Venue   10th Most Common Venue  Colleges  Cluster Labels  
0    Dumpling Restaurant  Fruit & Vegetable Store         2               0  
1      Korean Restaurant              Snack Place         1               3  
2          Movie Theater                    Motel         1               4  
3          Movie Theater                 Mountain         1               3  
4     Italian Restaurant         Asian Restaurant         2               0  
5          Movie Theater                 Mountain         1               1  
6      Convenience Store       Mexican Restaurant         4               2  
7          Movie Theater                 Mountain         2               0  
8                 Office                Multiplex       

##### Now, we'll visualize the resulting cluster

In [87]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)#Location of Pune city

# set color scheme for the clusters
colors=['red', 'yellow', 'orange', 'green', 'blue']

# add markers to the map
markers_colors = []
for lat, lng, neighborhood,cluster in zip(Pune_merged['Latitude'], Pune_merged['Longitude'],Pune_merged['Neighborhood'],Pune_merged['Cluster Labels']):
    label =  folium.Popup(str(neighborhood) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color=colors[cluster-1],
        fill=True,
        fill_color=colors[cluster-1],
        fill_opacity=0.5,
        parse_html=False).add_to(map_clusters)
map_clusters

##### Let's see how much registers there are in each cluster.



In [79]:
for cluster in np.sort(Pune_merged['Cluster Labels'].unique()):
    print(f'There are {Pune_merged.loc[Pune_merged["Cluster Labels"] == cluster].shape[0]} registers on Cluster {cluster}')

There are 3 registers on Cluster 0
There are 2 registers on Cluster 1
There are 1 registers on Cluster 2
There are 4 registers on Cluster 3
There are 1 registers on Cluster 4


##### Now, let's examine each cluster to find out more about it.



#### Cluster 1

In [81]:
Pune_merged.loc[Pune_merged['Cluster Labels'] == 0, Pune_merged.columns[[0] + list(range(3, Pune_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
45          Akurdi     Indian Restaurant                  Café   
41      Dhankawadi             Multiplex     Indian Restaurant   
43  Lavale Village     Indian Restaurant                Bakery   

   3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
45           Coffee Shop  South Indian Restaurant        Clothing Store   
41                Lounge              Coffee Shop        Clothing Store   
43                   Gym                   Office   American Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
45      Asian Restaurant   American Restaurant            Donut Shop   
41    Chinese Restaurant             Bookstore              Pharmacy   
43    Mexican Restaurant       Organic Grocery             Multiplex   

   9th Most Common Venue   10th Most Common Venue  Colleges  Cluster Labels  
45   Dumpling Restaurant  Fruit & Vegetable Store         2               0  
41    Italian Restaurant         Asian Restaurant         2               0  
43         Movie Theater                 Mountain         2               0

#### Cluster 2

In [82]:
Pune_merged.loc[Pune_merged['Cluster Labels'] == 1, Pune_merged.columns[[0] + list(range(3, Pune_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
46  Fergusson College Road                  Café          Home Service   
36             Viman Nagar  Gym / Fitness Center                  Café   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
46  Indian Chinese Restaurant     Indian Restaurant     Mobile Phone Shop   
36        American Restaurant    Mexican Restaurant       Organic Grocery   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
46       Organic Grocery                Office             Multiplex   
36                Office             Multiplex         Movie Theater   

   9th Most Common Venue 10th Most Common Venue  Colleges  Cluster Labels  
46         Movie Theater               Mountain         1               1  
36              Mountain                  Motel         1               1

#### Cluster 3


In [83]:
Pune_merged.loc[Pune_merged['Cluster Labels'] == 2, Pune_merged.columns[[0] + list(range(3, Pune_merged.shape[1]))]]


Neighborhood 1st Most Common Venue          2nd Most Common Venue  \
20      Kothrud        Breakfast Spot  Vegetarian / Vegan Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
20     Indian Restaurant           Pizza Place    Italian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
20        Ice Cream Shop            Restaurant                Lounge   

   9th Most Common Venue 10th Most Common Venue  Colleges  Cluster Labels  
20     Convenience Store     Mexican Restaurant         4               2

#### Cluster 4

In [84]:
Pune_merged.loc[Pune_merged['Cluster Labels'] == 3, Pune_merged.columns[[0] + list(range(3, Pune_merged.shape[1]))]]


Neighborhood          1st Most Common Venue 2nd Most Common Venue  \
1       Balewadi              Indian Restaurant   Sporting Goods Shop   
49        Deccan  Vegetarian / Vegan Restaurant         Shopping Mall   
47  Model Colony                    Pizza Place     Indian Restaurant   
44        Mulshi  Vegetarian / Vegan Restaurant            Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1   Fast Food Restaurant           Bus Station     Mobile Phone Shop   
49  Fast Food Restaurant    Chinese Restaurant           Pizza Place   
47    Chinese Restaurant  Fast Food Restaurant          Dance Studio   
44       Bed & Breakfast     Mobile Phone Shop    Mexican Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1         Ice Cream Shop                 Plaza         Grocery Store   
49    Tex-Mex Restaurant       Organic Grocery             Multiplex   
47                 Motel                  Park       Organic Grocery   
44       Organic Grocery                Office             Multiplex   

   9th Most Common Venue 10th Most Common Venue  Colleges  Cluster Labels  
1      Korean Restaurant            Snack Place         1               3  
49         Movie Theater               Mountain         1               3  
47                Office              Multiplex         1               3  
44         Movie Theater               Mountain         1               3

#### Cluster 5

In [85]:
Pune_merged.loc[Pune_merged['Cluster Labels'] == 4, Pune_merged.columns[[0] + list(range(3, Pune_merged.shape[1]))]]


Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
3      Bavdhan     Indian Restaurant    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3              Mountain   American Restaurant    Mexican Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
3       Organic Grocery                Office             Multiplex   

  9th Most Common Venue 10th Most Common Venue  Colleges  Cluster Labels  
3         Movie Theater                  Motel         1               4

# Result and Discussion

#### We found out that although there are many neighborhoods in Pune but we wanted the ones with famous colleges so that the clients can open a hostel or PG(Paying Guest) over there for students who migrate from different cities to Pune for their higher education and need a place to stay.

#### Thus, according to our analysis,there are 11 main neighborhoods where hostels can be opened.
#### We got this data by analysing top venues for each neighborhood in Pune and then filtering only those neighborhoods where there are famous colleges.
#### Then, we clustered the neighborhoods and found out that Akurdi, Dhankawadi, Lavale Village are clustered in one type of neighborhood  ;while Balewadi,Deccan,Model Colony,Mulshi	are clusterd in other type of neighborhood and likewise similar type of neighborhoods were clustered together.

# Conclusion

#### The objectiive of this project was to find the most suitable location in Pune to open a hostel for college students. 
#### Hence, after analysis, we found 11 most suitable neighborhoods to open a hostel at ;and now, its upto client to go the through details provided for each neighborhood and choose the the neighborhood which fits in the requirement.

#### We suggest Kothrud,Akurdi, Dhankawadi, Lavale Village as the most suitable neighborhoods among the top 11.